In [3]:
%load_ext autoreload
%autoreload 2
%matplotlib inline  

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.offline as pl
pl.init_notebook_mode(connected=True)
import plotly.graph_objs as go

from datetime import datetime, timedelta
import parseIntervalFiles as pif
import parseActivityFiles as paf
#pun intended :)
import consolidateFiles as cf
import datacleaning as cl

## Plotting random samples of each activity

In [8]:
verbose = True

PATH = "C:\\Users\\ju\\GDrive\\Projects\\HeRV\\Data\\"
RAW = PATH + "Raw"
file = PATH + "PreProcessed\\sessions.xlsx"

In [6]:
df = pd.read_excel(file)
df.sample(5)

activity  beatscount  duration           hf       hfnu  \
319        exercise        6356      2494   374.243151  60.253260   
188             eat         776       630   522.551270  25.152441   
116             eat        1007       571   767.739789  50.384478   
182  focused-active        5567      4264   239.349183  12.102957   
200           sleep        1544      1620  1729.032983  44.759489   

              lf     lf_hf       lfnu         mhr         mrri     ...       \
319   246.873701  0.659661  39.746740  155.541355   400.374921     ...        
188  1554.985732  2.975757  74.847559   85.104693   710.458763     ...        
116   756.022732  0.984738  49.615522  106.416750   573.723932     ...        
182  1738.259911  7.262443  87.897043   77.035338   784.263338     ...        
200  2133.908778  1.234163  55.240511   56.841248  1073.798575     ...        

     posture removed_artifacts      rmssd        sdnn  sess_id  \
319    stand                18  43.311362   90.201510      319   
188      sit                 0  36.732705   63.056336      188   
116      sit                21  70.780525   69.528698      116   
182      sit                 0  30.084651   64.340042      182   
200      lie                 1  73.049868  131.349618      200   

                  start                stop  total_power user          vlf  
319 2017-11-01 06:44:25 2017-11-01 07:25:59   843.183819    3   222.066966  
188 2018-01-21 17:05:00 2018-01-21 17:15:30  2769.390676    1   691.853674  
116 2017-11-05 12:40:44 2017-11-05 12:50:15  1950.061938    0   426.299417  
182 2017-11-04 03:12:36 2017-11-04 04:23:40  2802.723710    1   825.114616  
200 2017-09-30 03:32:00 2017-09-30 03:59:00  9226.153305    2  5363.211544  

[5 rows x 23 columns]

## Plotting random examples of RR time series for each type of activity

In [16]:
def plot_series(start, stop, user, title='timeseries'):
    """
    plots the series of RR intervals for user between start and stop datetimes
    """
    
    dirname = RAW + "\\" + str(user)
    rr = pif.get_intervals(start, stop, dirname)    
    rr = cl.clean_rr_series(rr)
    x1, x2 = cf.beats_to_lists(rr)

    trace1 = [go.Scatter(x=x1, y=x2)]
    trace2 = [go.Histogram(x=x2)]
    
    layout = go.Layout(title=title)

    pl.iplot(trace1, layout)
    pl.iplot(trace2, layout)

In [20]:
def plot_sess_rr(sess, title):
    """    
    sess can be a row from df or dic containing an 'rr' key with a list of beats (in dic form)
    """
    plot_series(sess['start'], sess['stop'], sess['user'])

In [21]:
for act in df['activity'].unique():
    v = df[df['activity'] == act].sample(1)
    print('---------------- ',act,' ---------------')
    for i in range(1):
        print('USER: ', v.iloc[i]['user'])
        plot_sess_rr(v.iloc[i], act)

----------------  focused-active  ---------------
USER:  1


----------------  leisure-active  ---------------
USER:  0


----------------  eat  ---------------
USER:  0


----------------  movement  ---------------
USER:  0


----------------  leisure-passive  ---------------
USER:  4


...

----------------  rest-passive  ---------------
USER:  5


----------------  rest-active  ---------------
USER:  0


----------------  household-chores  ---------------
USER:  0


----------------  focused-passive  ---------------
USER:  2


----------------  exercise  ---------------
USER:  3


## Plotting features summary for each type of session
---

In [27]:
df[df['activity'] == 'focused-passive'].hf

21     2837.424468
22      927.828746
23     5292.319028
30     6263.714609
31     4199.343576
39     3145.571540
47      320.329992
98      278.330250
107     341.434650
134     701.291136
135    1188.927908
170     408.553560
171     366.781559
172     749.037005
173     393.365358
212    1639.893215
216      63.435880
217     115.619983
218     167.348438
219     280.642040
220     451.853582
221     582.732962
222     496.446108
223     434.305421
224     734.571382
225     638.554469
226     753.913992
227    1078.820732
228     802.501594
229     551.248166
238     119.684466
239     202.944504
240     263.450615
241     379.340709
242      85.214999
276     780.105700
307     489.360259
Name: hf, dtype: float64

## Assessing how features evolve within a session
---